In [26]:
#!pip install preprocessor
!pip install vaderSentiment

     |████████████████████████████████| 5.8MB 3.0MB/s eta 0:00:01
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
    Preparing wheel metadata ... done
  Using cached https://files.pythonhosted.org/packages/08/82/917eb137b3e85060e4f7c8dc991fccfafb47aa1f6f59fdd63f406159b03e/murmurhash-1.0.5-cp37-cp37m-manylinux1_x86_64.whl
  Using cached https://files.pythonhosted.org/packages/af/6e/0605ffc1c3861cce4d029a9724f302232f993fe9d0dc6c04fb7bc49b7852/preshed-3.0.5-cp37-cp37m-manylinux1_x86_64.whl
  Using cached https://files.pythonhosted.org/packages/86/85/40b8f66c2dd8f4fd9f09d59b22720cffecf1331e788b8a0cab5bafb353d1/plac-1.1.3-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/6c/f9/9a5658e2f56932e41eb264941f9a2cb7f3ce41a80cb36b2af6ab78e2f8af/catalogue-1.0.0-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/8a/54/115f0c28a61d56674c3a5e05c46d6c3523ad196e1dcd3e2d8b

In [2]:
from elasticsearch import Elasticsearch 

from tweepy import OAuthHandler
from tweepy.streaming import StreamListener
import tweepy

#to obtain polarity and subjectivity of texts
from textblob import TextBlob
#to obtain the sentiment (pos,neg,neu) values
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer
#text cleaning
import spacy 

import string
#import preprocessor as p
import os
import time
import json
import pandas as pd
import numpy as np
import csv
from datetime import datetime
import re
from collections import Counter

In [2]:
# Connect to the elastic cluster
es=Elasticsearch([{'host':'localhost','port':9200}], timeout=30)
print(es)

<Elasticsearch([{'host': 'localhost', 'port': 9200}])>


# Authenticating Twitter API

If you ran into any authentication errors, regenerate your keys and try again

In [4]:
# Twitter credentials
# Obtain them from your twitter developer account
#TODO: delete keys before pushing to github

consumer_key = ""
consumer_secret = ""
access_key =""
access_secret = ""

# Pass your twitter credentials to tweepy via its OAuthHandler
auth = OAuthHandler(consumer_key, consumer_secret)
auth.set_access_token(access_key, access_secret)
api = tweepy.API(auth,wait_on_rate_limit=True) #add wait_on_rate_limit to avoid the rate limit error

# Method 1: Extract tweets using tweepy.Cursor. 
This Doesn't work

# Batch Scraping

Due to the limited number of API calls one can make using a basic and free developer account, (~900 calls every 15 minutes before your access is denied) I created a function that extract 2,500 tweets per run once every 15 minutes (I tried to extract 3,00 and above but that got me denied after the second batch). In this function you specify the:
1. search parameter such as key words and hashtags etc.
2. starting date, after which all tweets would be extracted (you can only extract tweets that are not older than the last 7 days)
3. number of tweets to pull per run
4. number of runs - each run happends once every 15 minutes

You may explore the list of metadata from the tweepy.Cursor object in detail (this is the real messy part).


In [43]:
def scraptweets(search_words, date_since, date_until, numTweets, numRuns):
    
    # Define a for-loop to generate tweets at regular intervals
    # We cannot make large API call in one go. Hence, let's try T times
    
    # Define a pandas dataframe to store the date:
    db_tweets = pd.DataFrame(columns = ['username', 'acctdesc', 'location', 'following',
                                        'followers', 'totaltweets', 'usercreatedts', 'tweetcreatedts',
                                        'retweetcount', 'tweet', 'hashtags']
                                )
    program_start = time.time()
    for i in range(0, numRuns):
        # We will time how long it takes to scrape tweets for each run:
        start_run = time.time()
        
        # Collect tweets using the Cursor object
        # .Cursor() returns an object that you can iterate or loop over to access the data collected.
        # Each item in the iterator has various attributes that you can access to get information about each tweet
        tweets = tweepy.Cursor(api.search, q=search_words, lang="en", since=date_since, tweet_mode='extended').items(numTweets)
# Store these tweets into a python list
        tweet_list = [tweet for tweet in tweets]
# Obtain the following info (methods to call them out):
        # user.screen_name - twitter handle
        # user.description - description of account
        # user.location - where is he tweeting from
        # user.friends_count - no. of other users that user is following (following)
        # user.followers_count - no. of other users who are following this user (followers)
        # user.statuses_count - total tweets by user
        # user.created_at - when the user account was created
        # created_at - when the tweet was created
        # retweet_count - no. of retweets
        # (deprecated) user.favourites_count - probably total no. of tweets that is favourited by user
        # retweeted_status.full_text - full text of the tweet
        # tweet.entities['hashtags'] - hashtags in the tweet
# Begin scraping the tweets individually:
        noTweets = 0
        for tweet in tweet_list:
            #ignore tweets not between date_since and date_until
            if tweet.created_at<date_since or tweet.created_at>date_until:
                continue
            
            #if tweet in valid date range
            # Pull the values
            username = tweet.user.screen_name
            acctdesc = tweet.user.description
            location = tweet.user.location
            following = tweet.user.friends_count
            followers = tweet.user.followers_count
            totaltweets = tweet.user.statuses_count
            usercreatedts = tweet.user.created_at
            tweetcreatedts = tweet.created_at
            retweetcount = tweet.retweet_count
            hashtags = tweet.entities['hashtags']
            try:
                Tweet = tweet.retweeted_status.full_text
            except AttributeError:  # Not a Retweet
                Tweet = tweet.full_text
# Add the 11 variables to the empty list - ith_tweet:
            ith_tweet = [username, acctdesc, location, following, followers, totaltweets,
                         usercreatedts, tweetcreatedts, retweetcount, Tweet, hashtags]
# Append to dataframe - db_tweets
            db_tweets.loc[len(db_tweets)] = ith_tweet
# increase counter - noTweets  
            noTweets += 1
        
        # Run ended:
        end_run = time.time()
        duration_run = round((end_run-start_run)/60, 2)
        
        print('no. of tweets scraped for run {} is {}'.format(i + 1, noTweets))
        print('time take for {} run to complete is {} mins'.format(i+1, duration_run))
        
        #time.sleep(920) #15 minute sleep time
        time.sleep(5) #reducing sleep time to get results faster
        
# Once all runs have completed, save them to a single csv file:
    from datetime import datetime
    
    # Obtain timestamp in a readable format
    to_csv_timestamp = datetime.today().strftime('%Y%m%d_%H%M%S')
# Define working path and filename
    path = os.getcwd()
    filename = path + '/tweets/' + to_csv_timestamp + '_stock_tweets.csv'
    
    # Store dataframe in csv with creation date timestamp
    db_tweets.to_csv(filename, index = False)
    
    program_end = time.time()
    print('Scraping has completed!')
    print('Total time taken to scrap is {} minutes.'.format(round(program_end - program_start)/60, 2))

In [50]:
#call the scraptweets function with required paramaeters
search_words = 'elon musk OR nytimes OR washingtonpost OR goldmansachs OR #financial news OR stock OR wall street'
date_since = datetime(2020, 12, 1, 0, 0, 0)
date_until = datetime(2020, 12, 11, 0, 0, 0)
numTweets = 1000
numRuns=3

scraptweets(search_words,date_since,date_until,numTweets,numRuns)

#additional info:
#to scrap specific user profiles
#ANJAN, if you ever see this, its creepy I know :P
#tweets = tweepy.Cursor(api.user_timeline, screen_name='anjanragh21').pages()

no. of tweets scraped for run 1 is 0
time take for 1 run to complete is 0.02 mins
no. of tweets scraped for run 2 is 0
time take for 2 run to complete is 0.01 mins
no. of tweets scraped for run 3 is 0
time take for 3 run to complete is 0.01 mins
Scraping has completed!
Total time taken to scrap is 0.2833333333333333 minutes.


# Method 2: Extract tweets using stream
This works but cannot extract tweets between start and end date. Only one day tweets are obtained. 

In [5]:
from tweepy import API, Stream, OAuthHandler, TweepError

def date_range(start,end):
    current = start
    while (end - current).days >= 0:
        yield current
        current = current + datetime.timedelta(seconds=1)
        
class TweetStreamListener(StreamListener):
    def __init__(self):
        self.count = 0
        self.count_filtered = 0
        self.filter_ratio = 0
        self.db_tweets=pd.DataFrame(columns = ['user_name', 'location', 'friends', 'followers', 
                                               'created_date', 'text_raw'])
        
    # on success
    def on_data(self, data):
        self.count+=1
        # decode json
        dict_data = json.loads(data)
        #print("\n------------------------------> (tweets: %s, filtered: %s, filter-ratio: %s)" \
        #        % (self.count, self.count_filtered, str(round(self.count_filtered/self.count*100,2))+"%"))
        text = dict_data['text']
        
        # get date when tweet was created
        created_date = time.strftime(
                '%Y-%m-%dT%H:%M:%S', time.strptime(dict_data['created_at'], '%a %b %d %H:%M:%S +0000 %Y'))
                                   
        # store dict_data into vars
        user_name = str(dict_data.get("user", {}).get("screen_name"))
        location = str(dict_data.get("user", {}).get("location"))
        language = str(dict_data.get("user", {}).get("lang"))
        friends = int(dict_data.get("user", {}).get("friends_count"))
        followers = int(dict_data.get("user", {}).get("followers_count"))
        statuses = int(dict_data.get("user", {}).get("statuses_count"))
        tweetid = int(dict_data.get("id"))
        text_raw = str(dict_data.get("text"))

        # output twitter data
        print("\n<------------------------------")
        print("Tweet Date: " + created_date)
        print("User Name: " + user_name)
        print("Location: " + location)
        print("Language: " + language)
        print("Friends: " + str(friends))
        print("Followers: " + str(followers))
        print("Statuses: " + str(statuses))
        print("Tweet ID: " + str(tweetid))
        print("Tweet Raw Text: " + text_raw)
        
        # Add the variables to the empty list - ith_tweet:
        ith_tweet = [user_name, location, friends, followers,
                      created_date, text_raw]
        # Append to dataframe - db_tweets or add to elastic search db if needed
        self.db_tweets.loc[len(self.db_tweets)] = ith_tweet
        
        #save the df - operation inefficient as it saves for every tweet
        self.db_tweets.to_csv('tweets/stock_tweets.csv',index=False)
        # increase counter - noTweets  
        self.count+=1
        
        
            
# create instance of the tweepy tweet stream listener
tweetlistener = TweetStreamListener()

# create instance of the tweepy stream
stream = Stream(auth,tweetlistener)

keywords=['elon', 'musk', 'stock', 'stock market', 'wall street', 'new york stock exchange']
stream.filter(track=keywords, languages=['en'])


<------------------------------
Tweet Date: 2020-12-14T16:53:25
User Name: SurfingMarty
Location: San Diego,  California
Language: None
Friends: 5001
Followers: 2486
Statuses: 63143
Tweet ID: 1338527524704272385
Tweet Raw Text: @BellsInequality Stock up

<------------------------------
Tweet Date: 2020-12-14T16:53:25
User Name: _Actice_
Location: United States
Language: None
Friends: 247
Followers: 19
Statuses: 38957
Tweet ID: 1338527524830195715
Tweet Raw Text: RT @bubblu_: i love this stock photo every time i see it https://t.co/y11l4JsQxd

<------------------------------
Tweet Date: 2020-12-14T16:53:25
User Name: paulabb42775833
Location: Alton, England
Language: None
Friends: 382
Followers: 56
Statuses: 2457
Tweet ID: 1338527525568385028
Tweet Raw Text: RT @gatewaypundit: REVEALED: SolarWinds Director Sold $45.7 MILLION in Stock Options Last Week Before CISA Announcement Sunday via @gateway…

<------------------------------
Tweet Date: 2020-12-14T16:53:25
User Name: CarlaJoSoBoCo



<------------------------------
Tweet Date: 2020-12-14T16:53:30
User Name: jblackwell787
Location: California 
Language: None
Friends: 1575
Followers: 530
Statuses: 12769
Tweet ID: 1338527548456648704
Tweet Raw Text: RT @Scrufey21Me: REVEALED: SolarWinds Director Sold $45.7 MILLION in Stock Options Last Week Before CISA Announcement Sunday https://t.co/v…

<------------------------------
Tweet Date: 2020-12-14T16:53:31
User Name: corvid317
Location: USA
Language: None
Friends: 3765
Followers: 2804
Statuses: 12004
Tweet ID: 1338527550864158720
Tweet Raw Text: Attack on Jill Biden's 'Dr.' title is no surprise for women scholars -- and proof that she needs to use it (Opinion… https://t.co/ExrZG3ymiM

<------------------------------
Tweet Date: 2020-12-14T16:53:31
User Name: Elijah_Is_John
Location: Chattanooga & Atlanta 
Language: None
Friends: 19350
Followers: 18777
Statuses: 173011
Tweet ID: 1338527551610908675
Tweet Raw Text: RT @shana0326: Insider Trading https://t.co/Va6dOFmh1Y

<--


<------------------------------
Tweet Date: 2020-12-14T16:53:36
User Name: investor1927
Location: None
Language: None
Friends: 769
Followers: 70
Statuses: 17803
Tweet ID: 1338527572779524096
Tweet Raw Text: RT @chamath: For those of you who invested in $DM, the last day saw serious trading issues. 

A company that the NYSE uses to help manage C…

<------------------------------
Tweet Date: 2020-12-14T16:53:36
User Name: HoneydewHeart
Location: None
Language: None
Friends: 791
Followers: 84
Statuses: 4413
Tweet ID: 1338527573672747008
Tweet Raw Text: RT @Orquidiart: Bisexuality

<------------------------------
Tweet Date: 2020-12-14T16:53:37
User Name: TopYields
Location: None
Language: None
Friends: 63
Followers: 1403
Statuses: 137916
Tweet ID: 1338527574411128834
Tweet Raw Text: The stock with the highest #dividend #yield (7.32%) of the FTSE #MIB (Italy) is UNIPOLSAI https://t.co/tAZ6ufEEKs

<------------------------------
Tweet Date: 2020-12-14T16:53:37
User Name: ETCTodayNews
Locat


<------------------------------
Tweet Date: 2020-12-14T16:53:41
User Name: jpmsxo
Location: Pennsylvania, USA
Language: None
Friends: 5000
Followers: 3045
Statuses: 125593
Tweet ID: 1338527594992574464
Tweet Raw Text: REVEALED: SolarWinds Director Sold $45.7 MILLION in Stock Options Last Week Before CISA Announcement Sunday… https://t.co/wlqNEPbMBl

<------------------------------
Tweet Date: 2020-12-14T16:53:42
User Name: angelrains
Location: Kraken
Language: None
Friends: 5771
Followers: 5174
Statuses: 46194
Tweet ID: 1338527595743203328
Tweet Raw Text: RT @disclosetv: JUST IN - SolarWinds CEO, CFO, and directors reportedly sold $15,000,000 worth of stock in November 2020. https://t.co/S4G2…

<------------------------------
Tweet Date: 2020-12-14T16:53:43
User Name: Philip74713096
Location: North Carolina, USA
Language: None
Friends: 318
Followers: 416
Statuses: 19869
Tweet ID: 1338527600403156992
Tweet Raw Text: RT @intheMatrixxx: REVEALED: SolarWinds Director Sold $45.7 MILLION in


<------------------------------
Tweet Date: 2020-12-14T16:53:48
User Name: Erica7016
Location: United States of America 
Language: None
Friends: 6580
Followers: 6411
Statuses: 7647
Tweet ID: 1338527620900646913
Tweet Raw Text: RT @MattHookNY: Wow! A call for martial law!

 Next several days are going to be a wild ride!

Strap onto your seats  and get the popcorn r…

<------------------------------
Tweet Date: 2020-12-14T16:53:48
User Name: ProjectSeaStar
Location: None
Language: None
Friends: 1327
Followers: 634
Statuses: 4950
Tweet ID: 1338527622331060225
Tweet Raw Text: RT @nytimes: A controversial opinion piece in the Wall Street Journal suggested that Dr. Jill Biden — who holds a doctorate in education an…

<------------------------------
Tweet Date: 2020-12-14T16:53:48
User Name: suzola2
Location: Reno, NV.
Language: None
Friends: 743
Followers: 400
Statuses: 17591
Tweet ID: 1338527622746128385
Tweet Raw Text: RT @gatewaypundit: REVEALED: SolarWinds Director Sold $45.7 MILLION in

...


<------------------------------
Tweet Date: 2020-12-14T18:03:58
User Name: KlonnieChron
Location: None
Language: None
Friends: 822
Followers: 1595
Statuses: 25829
Tweet ID: 1338545278547181572
Tweet Raw Text: @KT_So_It_Goes to be fair (?) I did stock up on essentials in case they go even more nuts this week/month/year but… https://t.co/wF2XJTo7tV

<------------------------------
Tweet Date: 2020-12-14T18:03:58
User Name: LosKidsVenice
Location: California, USA
Language: None
Friends: 135
Followers: 43
Statuses: 6789
Tweet ID: 1338545279671312384
Tweet Raw Text: RT @donwinslow: Dear @Twitter and @TwitterSafety 

This man is urging people to stock up on guns and ammo for a civil war ON YOUR PLATFORM.…

<------------------------------
Tweet Date: 2020-12-14T18:03:58
User Name: NantosueltaE
Location: Los Angeles & Dublin
Language: None
Friends: 288
Followers: 16
Statuses: 34
Tweet ID: 1338545280304574465
Tweet Raw Text: RT @WSJ: “I think there might be too many M.B.A.s running companies,”


<------------------------------
Tweet Date: 2020-12-14T18:04:04
User Name: HarmonyFreya
Location: Colorado, USA
Language: None
Friends: 1651
Followers: 1593
Statuses: 2893
Tweet ID: 1338545306036682754
Tweet Raw Text: @WipeOffYourChin @itsgatstabebet1 @caligrl1959 @tahoqueen22 @realDonaldTrump I’ll wait for you to explain what his… https://t.co/V2E9OiCptX

<------------------------------
Tweet Date: 2020-12-14T18:04:05
User Name: thatonepinkslut
Location: alternia
Language: None
Friends: 432
Followers: 97
Statuses: 36656
Tweet ID: 1338545308947591171
Tweet Raw Text: RT @ChristinaTasty: Cyberpunk was a victim of its own hype. 

Witcher 3 came out of nowhere and sold TWENTY TIMES more than its sequel in t…

<------------------------------
Tweet Date: 2020-12-14T18:04:05
User Name: MaximumBurner
Location: VFX Paradise
Language: None
Friends: 298
Followers: 275
Statuses: 8849
Tweet ID: 1338545311061598208
Tweet Raw Text: RT @disclosetv: JUST IN - SolarWinds CEO, CFO, and directors reporte


<------------------------------
Tweet Date: 2020-12-14T18:04:12
User Name: Bts_Army97_95
Location: Florida, USA
Language: None
Friends: 127
Followers: 255
Statuses: 9621
Tweet ID: 1338545340342018057
Tweet Raw Text: Omg  🤦🏾‍♀️. If it’s not one thing it’s another.

<------------------------------
Tweet Date: 2020-12-14T18:04:12
User Name: randomirish
Location: Anarchist Jurisdiction 
Language: None
Friends: 1992
Followers: 1737
Statuses: 27169
Tweet ID: 1338545341185069056
Tweet Raw Text: RT @SykesCharlie: Trump loses the Wall Street Journal. https://t.co/l8FTcH9yl1 via @WSJ

<------------------------------
Tweet Date: 2020-12-14T18:04:13
User Name: thrustlimbaugh
Location: United States
Language: None
Friends: 778
Followers: 535
Statuses: 1285
Tweet ID: 1338545342502100994
Tweet Raw Text: @DrBiden You aren’t a pioneer of anything.  Nobidy is or ever has been excited about you or your preinstalled, stock “ideas”.

<------------------------------
Tweet Date: 2020-12-14T18:04:13
User Nam


<------------------------------
Tweet Date: 2020-12-14T18:04:19
User Name: Kreedo8
Location: None
Language: None
Friends: 131
Followers: 12
Statuses: 2215
Tweet ID: 1338545368729051136
Tweet Raw Text: RT @gatewaypundit: REVEALED: SolarWinds Director Sold $45.7 MILLION in Stock Options Last Week Before CISA Announcement Sunday via @gateway…

<------------------------------
Tweet Date: 2020-12-14T18:04:19
User Name: gladweleft
Location: Not a good place
Language: None
Friends: 2445
Followers: 1970
Statuses: 41971
Tweet ID: 1338545369437835272
Tweet Raw Text: RT @gatewaypundit: REVEALED: SolarWinds Director Sold $45.7 MILLION in Stock Options Last Week Before CISA Announcement Sunday via @gateway…

<------------------------------
Tweet Date: 2020-12-14T18:04:19
User Name: chananacakes
Location: Always in the same spot
Language: None
Friends: 243
Followers: 288
Statuses: 53183
Tweet ID: 1338545370671017984
Tweet Raw Text: RT @Ryan_Ken_Acts: Apply for the job, opportunity, etc. Go for it. 

ProtocolError: ('Connection broken: IncompleteRead(0 bytes read)', IncompleteRead(0 bytes read))

# Method 3: Extract tweets between start and end date from usernames
Great! Finally got what i wanted on the third try. Use this to extract tweets from twitter usernames between start and end date

In [11]:
#provide the username
username = "NYSE"
startDate = datetime(2020, 12, 1, 0, 0, 0)
endDate =   datetime(2020, 12, 12, 0, 0, 0)

tweets = []
tmpTweets = api.user_timeline(username)
for tweet in tmpTweets:
    if tweet.created_at < endDate and tweet.created_at > startDate:
        tweets.append(tweet)

while (tmpTweets[-1].created_at > startDate):
    print("Last Tweet @", tmpTweets[-1].created_at, " - fetching some more")
    tmpTweets = api.user_timeline(username, max_id = tmpTweets[-1].id)
    for tweet in tmpTweets:
        if tweet.created_at < endDate and tweet.created_at > startDate:
            tweets.append(tweet)

#save tweets to csv file           
db_tweets = pd.DataFrame(columns=['createdAt', 'username', 'location', 'tweetId', 'rawTweet'])

for tweet in tweets:
    createdAt = tweet.created_at
    username = tweet.user.screen_name
    location = tweet.user.location
    tweetId = tweet.id
    rawTweet = tweet.text
    
    print("createdAt", createdAt)
    print("username",username)
    print("raw tweet", rawTweet)
    
    # Add the variables to the empty list - ith_tweet:
    ith_tweet = [createdAt, username, location, tweetId, rawTweet]
    # Append to dataframe - db_tweets or add to elastic search db if needed
    db_tweets.loc[len(db_tweets)] = ith_tweet

#save the df
db_tweets.to_csv('tweets/stock_tweets_'+username+'.csv',index=False)
    

Last Tweet @ 2020-12-10 15:00:02  - fetching some more
Last Tweet @ 2020-12-08 19:02:30  - fetching some more
Last Tweet @ 2020-12-04 21:32:37  - fetching some more
Last Tweet @ 2020-12-02 15:45:57  - fetching some more
createdAt 2020-12-11 23:12:05
username NYSE
raw tweet RT @AssetTVUS: 2020 has seen the launch of a lot of new actively managed #ETFs. Head of Exchange Traded Funds Tim Coyne shares why @TRowePr…
createdAt 2020-12-11 21:50:06
username NYSE
raw tweet How it started ➡️ How it's going https://t.co/7FZ8gJPmdj
createdAt 2020-12-11 21:30:00
username NYSE
raw tweet Northern Trust Asset Management's Michael Natale tells us about HYGV, the @FlexsharesETFs High Yield Value-Scored B… https://t.co/R0pYq9RA8u
createdAt 2020-12-11 21:07:26
username NYSE
raw tweet RT @SempraEnergy: Thank you @SPGlobalPlatts for recognizing Sempra Energy with CEO of the Year and Deal of the Year Awards. #PlattsGEA http…
createdAt 2020-12-11 20:59:12
username NYSE
raw tweet The NYSE welcomes Infosys (NYS

createdAt 2020-12-02 20:07:13
username NYSE
raw tweet .@Genpact is using its AI software to help the UK government track potential adverse events related to a future COV… https://t.co/SKL2hOwNzD
createdAt 2020-12-02 15:45:57
username NYSE
raw tweet Capitol Investment Corp. V (NYSE: CAP.U) officially opened on the New York Stock Exchange at $10.00
createdAt 2020-12-02 15:45:57
username NYSE
raw tweet Capitol Investment Corp. V (NYSE: CAP.U) officially opened on the New York Stock Exchange at $10.00
createdAt 2020-12-02 14:57:56
username NYSE
raw tweet NYSE President @Stacey_Cunning discusses the record-breaking IPO market in 2020 and the strong pipeline for 2021 at… https://t.co/P3afaIFtKq
createdAt 2020-12-02 14:29:12
username NYSE
raw tweet The NYSE welcomes The Aaron's Company (NYSE: AAN) in honor of their spin off from Aaron’s, Inc https://t.co/NNe5VIaFfp
createdAt 2020-12-01 22:37:26
username NYSE
raw tweet Congratulations to @salesforce and @SlackHQ as they combine to help compani

In [25]:
tweets_df = pd.read_csv('./tweets/stock_tweets_NYSE.csv')
print(tweets_df)


              createdAt username      location              tweetId  \
0   2020-12-11 23:12:05     NYSE  New York, NY  1337535655048597505   
1   2020-12-11 21:50:06     NYSE  New York, NY  1337515025355968512   
2   2020-12-11 21:30:00     NYSE  New York, NY  1337509967163654146   
3   2020-12-11 21:07:26     NYSE  New York, NY  1337504288646565893   
4   2020-12-11 20:59:12     NYSE  New York, NY  1337502217411018752   
..                  ...      ...           ...                  ...   
79  2020-12-01 21:26:46     NYSE  New York, NY  1333885276490489866   
80  2020-12-01 20:59:13     NYSE  New York, NY  1333878340768342016   
81  2020-12-01 15:00:00     NYSE  New York, NY  1333787942104416259   
82  2020-12-01 14:54:33     NYSE  New York, NY  1333786571405811712   
83  2020-12-01 14:29:18     NYSE  New York, NY  1333780217052106753   

                                             rawTweet  
0   RT @AssetTVUS: 2020 has seen the launch of a l...  
1   How it started ➡️ How it's goin

# Remove duplicates

In [14]:
#remove duplicate tweets
tweets_df = tweets_df.drop_duplicates(subset='rawTweet')
len(tweets_df)

80

# Split createdAt timestamp into date and time columns

In [28]:
tweets_df['date']=[d.split()[0] for d in tweets_df['createdAt']]
tweets_df['time']=[d.split()[1] for d in tweets_df['createdAt']]
tweets_df

createdAt username      location              tweetId  \
0   2020-12-11 23:12:05     NYSE  New York, NY  1337535655048597505   
1   2020-12-11 21:50:06     NYSE  New York, NY  1337515025355968512   
2   2020-12-11 21:30:00     NYSE  New York, NY  1337509967163654146   
3   2020-12-11 21:07:26     NYSE  New York, NY  1337504288646565893   
4   2020-12-11 20:59:12     NYSE  New York, NY  1337502217411018752   
..                  ...      ...           ...                  ...   
79  2020-12-01 21:26:46     NYSE  New York, NY  1333885276490489866   
80  2020-12-01 20:59:13     NYSE  New York, NY  1333878340768342016   
81  2020-12-01 15:00:00     NYSE  New York, NY  1333787942104416259   
82  2020-12-01 14:54:33     NYSE  New York, NY  1333786571405811712   
83  2020-12-01 14:29:18     NYSE  New York, NY  1333780217052106753   

                                             rawTweet        date      time  
0   RT @AssetTVUS: 2020 has seen the launch of a l...  2020-12-11  23:12:05  
1   How it started ➡️ How it's going https://t.co/...  2020-12-11  21:50:06  
2   Northern Trust Asset Management's Michael Nata...  2020-12-11  21:30:00  
3   RT @SempraEnergy: Thank you @SPGlobalPlatts fo...  2020-12-11  21:07:26  
4   The NYSE welcomes Infosys (NYSE: INFY) in cele...  2020-12-11  20:59:12  
..                                                ...         ...       ...  
79  It’s a December to remember as the S&amp;P ris...  2020-12-01  21:26:46  
80  The NYSE welcomes @salesforce to celebrate the...  2020-12-01  20:59:13  
81  He dropped out of school at age 14 and went on...  2020-12-01  15:00:00  
82  The S&amp;P 500 opened 1.15% higher, up 41.66 ...  2020-12-01  14:54:33  
83  The NYSE welomes @petrobras (NYSE: PBR) to cel...  2020-12-01  14:29:18  

[84 rows x 7 columns]

# Filter tweets in date range

In [68]:
# tweets_df = tweets_df.set_index(['created_date'])
# filtered_df = tweets_df.loc['2020-12-11','2020-12-13']
# filtered_df

KeyError: '2020-12-11'

# Text Cleaning

In [29]:
#load eng language
nlp = spacy.load('en_core_web_sm')

def normalise(msg): 
    doc = nlp(msg)
    res = []
    
    for token in doc:
        #Removing Stop words and words out of vocabulary
        if token.is_stop or token.is_punct or token.is_space or not(token.is_oov): 
            pass
        #lemmatize words
        #lemmatize example: going and went are converted to go.
        else:
            res.append(token.lemma_.lower())
    
    res = ' '.join(res)        
    return res

In [30]:
tweets_df['cleanTweet']=tweets_df['rawTweet'].apply(normalise)

## Most common words

In [31]:
words_collection = Counter([word for tweet in tweets_df['cleanTweet'] for word in tweet.split()])
freq_word_df = pd.DataFrame(words_collection.most_common(15))
freq_word_df.columns = ['frequently_used_word','count']

freq_word_df.style.background_gradient(cmap='YlGnBu', low=0, high=0, axis=0, subset=None)

# Subjectivity, Polarity and Sentiment of Tweets

In [32]:
#get subjectivity and polarity for tweets
def get_polarity(tweet):
    return TextBlob(tweet).sentiment.polarity

def get_subjectivity(tweet):
    return TextBlob(tweet).sentiment.subjectivity

In [33]:
#polarity ranges from -1 to 1, -1 is negative and 1 is positive
tweets_df['polarity']=tweets_df['cleanTweet'].apply(get_polarity)

#subjectivity ranges from 0 to 1. 0 is objective and 1 is subjective
tweets_df['subjectivity']=tweets_df['cleanTweet'].apply(get_subjectivity)

tweets_df

createdAt username      location              tweetId  \
0   2020-12-11 23:12:05     NYSE  New York, NY  1337535655048597505   
1   2020-12-11 21:50:06     NYSE  New York, NY  1337515025355968512   
2   2020-12-11 21:30:00     NYSE  New York, NY  1337509967163654146   
3   2020-12-11 21:07:26     NYSE  New York, NY  1337504288646565893   
4   2020-12-11 20:59:12     NYSE  New York, NY  1337502217411018752   
..                  ...      ...           ...                  ...   
79  2020-12-01 21:26:46     NYSE  New York, NY  1333885276490489866   
80  2020-12-01 20:59:13     NYSE  New York, NY  1333878340768342016   
81  2020-12-01 15:00:00     NYSE  New York, NY  1333787942104416259   
82  2020-12-01 14:54:33     NYSE  New York, NY  1333786571405811712   
83  2020-12-01 14:29:18     NYSE  New York, NY  1333780217052106753   

                                             rawTweet        date      time  \
0   RT @AssetTVUS: 2020 has seen the launch of a l...  2020-12-11  23:12:05   
1   How it started ➡️ How it's going https://t.co/...  2020-12-11  21:50:06   
2   Northern Trust Asset Management's Michael Nata...  2020-12-11  21:30:00   
3   RT @SempraEnergy: Thank you @SPGlobalPlatts fo...  2020-12-11  21:07:26   
4   The NYSE welcomes Infosys (NYSE: INFY) in cele...  2020-12-11  20:59:12   
..                                                ...         ...       ...   
79  It’s a December to remember as the S&amp;P ris...  2020-12-01  21:26:46   
80  The NYSE welcomes @salesforce to celebrate the...  2020-12-01  20:59:13   
81  He dropped out of school at age 14 and went on...  2020-12-01  15:00:00   
82  The S&amp;P 500 opened 1.15% higher, up 41.66 ...  2020-12-01  14:54:33   
83  The NYSE welomes @petrobras (NYSE: PBR) to cel...  2020-12-01  14:29:18   

                                           cleanTweet  polarity  subjectivity  
0   rt @assettvus 2020 see launch lot new actively...  0.001515      0.527273  
1                start ➡ ️ go https://t.co/7fz8gjpmdj  0.000000      0.000000  
2   northern trust asset management michael natale...  0.160000      0.540000  
3   rt @sempraenergy thank @spglobalplatts recogni...  0.000000      0.000000  
4   nyse welcome infosys nyse infy celebration 8th...  0.800000      0.900000  
..                                                ...       ...           ...  
79  december remember s&amp;p rise +1.13 reach rec...  0.160000      0.540000  
80  nyse welcome @salesforce celebrate global gene...  0.400000      0.450000  
81  drop school age 14 go serial entrepreneur co f...  0.000000      0.000000  
82  s&amp;p 500 open 1.15 high 41.66 point 3,663.2...  0.080000      0.520000  
83  nyse welome @petrobras nyse pbr celebrate 20th...  0.000000      0.000000  

[84 rows x 10 columns]

In [34]:
#get the sentiment scores
def get_sentiment(news):
    sia = SentimentIntensityAnalyzer()
    sentiment = sia.polarity_scores(news)
    return sentiment

In [35]:
compound,pos,neg,neu,sentiments = [],[],[],[],[]
for index,row in tweets_df.iterrows():
    sentiment = get_sentiment(tweets_df['cleanTweet'][index])
    pos.append(sentiment['pos'])
    neg.append(sentiment['neg'])
    neu.append(sentiment['neu'])
    #compound.append(sentiment['compound'])
  
    #find the maximum of pos,neg,neu and create target
    index = np.argmax([sentiment['neg'], sentiment['neu'], sentiment['pos']])
    #negative
    if index==0:
        sentiments.append('negative')
    #neutral
    elif index==1:
        sentiments.append('neutral')
    #positive
    else:
        sentiments.append('positive')  

tweets_df['positive']=pos
tweets_df['negative']=neg
tweets_df['neutral']=neu
#df['compound']=compound
tweets_df['sentiment']=sentiments
tweets_df.head()

createdAt username      location              tweetId  \
0  2020-12-11 23:12:05     NYSE  New York, NY  1337535655048597505   
1  2020-12-11 21:50:06     NYSE  New York, NY  1337515025355968512   
2  2020-12-11 21:30:00     NYSE  New York, NY  1337509967163654146   
3  2020-12-11 21:07:26     NYSE  New York, NY  1337504288646565893   
4  2020-12-11 20:59:12     NYSE  New York, NY  1337502217411018752   

                                            rawTweet        date      time  \
0  RT @AssetTVUS: 2020 has seen the launch of a l...  2020-12-11  23:12:05   
1  How it started ➡️ How it's going https://t.co/...  2020-12-11  21:50:06   
2  Northern Trust Asset Management's Michael Nata...  2020-12-11  21:30:00   
3  RT @SempraEnergy: Thank you @SPGlobalPlatts fo...  2020-12-11  21:07:26   
4  The NYSE welcomes Infosys (NYSE: INFY) in cele...  2020-12-11  20:59:12   

                                          cleanTweet  polarity  subjectivity  \
0  rt @assettvus 2020 see launch lot new actively...  0.001515      0.527273   
1               start ➡ ️ go https://t.co/7fz8gjpmdj  0.000000      0.000000   
2  northern trust asset management michael natale...  0.160000      0.540000   
3  rt @sempraenergy thank @spglobalplatts recogni...  0.000000      0.000000   
4  nyse welcome infosys nyse infy celebration 8th...  0.800000      0.900000   

   positive  negative  neutral sentiment  
0     0.220       0.0    0.780   neutral  
1     0.000       0.0    1.000   neutral  
2     0.406       0.0    0.594   neutral  
3     0.409       0.0    0.591   neutral  
4     0.250       0.0    0.750   neutral

In [36]:
# Obtain timestamp in a readable format
timestamp = datetime.today().strftime('%Y%m%d_%H%M%S')

tweets_df.to_csv('tweets_labelled/'+str(timestamp)+'_full_df.csv',index=False,header=True)

# References

https://medium.com/python-in-plain-english/scraping-tweets-with-tweepy-python-59413046e788

https://medium.com/python-in-plain-english/create-a-simple-covid-19-dashboard-with-flask-plotly-altair-chart-js-and-adminlte-a92ef86a3ca8